Course 5: Geographic Data Visualization
================

# 1. Geographic Data

There are several Python libraries specialized in visualizing geographic data, such as Folium, Cartopy, Basemap, etc.

Bokeh, while not specialized in mapping, also handles geographic data visualization quite well. Therefore, we will continue to use Bokeh for the rest of the course.

Documentation link: https://docs.bokeh.org/en/latest/docs/user_guide/topics/geo.html#geographical-data

Note: Throughout this notebook, we are using a specific functionality that allows direct display in the notebook rather than in a web page:


In [1]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

# 2. Simple Map with Bokeh

To create a map, we start by creating a regular Bokeh plot. Then, we need to:
- add a map background: `Tile`
- specify the use of geographic axes: `Axis type: mercator`

Here's an example map:


In [2]:
from bokeh.plotting import figure, show

# Create a figure with geographic axes
p = figure(x_axis_type="mercator", y_axis_type="mercator", title="First map", x_range=(-1000000, 1000000), y_range=(5500000, 6000000))

# Add a map background
p.add_tile("CartoDB Positron")

show(p)


You can zoom in on the map to view background details.

There are many map background providers: CartoDB Positron, OSM, Esri World Imagery (satellite view), etc.

For example, by changing the background map:

In [3]:
from bokeh.plotting import figure, show

p = figure(x_axis_type="mercator", y_axis_type="mercator", title="First map", x_range=(-1000000, 1000000), y_range=(5500000, 6000000))

p.add_tile("OSM")
show(p)



# 3. Point Coordinates

Now let's plot a point: the city of Rennes, for which we know the coordinates: `xrennes, yrennes = 1.6742900, 48.1119800`.

We just need to add a point plot to the diagram:


In [4]:
from bokeh.plotting import figure, show

p = figure(x_axis_type="mercator", y_axis_type="mercator", title="First map", x_range=(-2000000, 6000000), y_range=(-1000000, 7000000))
p.add_tile("OSM")

xrennes, yrennes = -1.6742900, 48.1119800
p.diamond(xrennes, yrennes, color='red', size=10)

show(p)

Problem: Rennes is placed in the sea south of Africa...

Indeed, GPS coordinates are spherical coordinates. To be displayed on a plane, they need to be converted.

We provide the conversion function `coor_wgs84_to_web_mercator`:

In [5]:
from bokeh.plotting import figure, show
import numpy as np

# Converts decimal longitude/latitude to Web Mercator format
def coor_wgs84_to_web_mercator(lon, lat):
    k = 6378137
    x = lon * (k * np.pi/180.0)
    y = np.log(np.tan((90 + lat) * np.pi/360.0)) * k
    return (x, y)

p = figure(x_axis_type="mercator", y_axis_type="mercator", title="First map", x_range=(-1000000, 1000000), y_range=(5500000, 6000000))
p.add_tile("OSM")

xrennes, yrennes = coor_wgs84_to_web_mercator(-1.6742900, 48.1119800)
p.diamond(xrennes, yrennes, color='red', size=10)
show(p)

This time, Rennes is correctly positioned!

So, it will be necessary to systematically use the coordinates conversion function.

# 4. Examples of Cartography

## 4.1 Capitals

In this example, we want to display the capitals of the world and allow hovering to visualize the name of the capital and the name of the country.

First, we need to find the source data, often available in geojson format. We can extract it as json data.

Here's the commented code:

In [6]:
from bokeh.plotting import figure, show
from bokeh.models import HoverTool, ColumnDataSource
import numpy as np
import json
import pandas

# Define the conversion function again
def coor_wgs84_to_web_mercator(lon, lat):
    k = 6378137
    x = lon * (k * np.pi/180.0)
    y = np.log(np.tan((90 + lat) * np.pi/360.0)) * k
    return (x, y)

# Read the JSON file: extracting country names, capitals, and coordinates
fp = open("capitals.geojson", "r", encoding='utf-8')
dico = json.load(fp)

country = []
capitale = []
coordx = []
coordy = []

# Prepare the construction of a DataFrame, converting coordinates
for p in dico["features"]:
    country.append(p["properties"]["country"])
    capitale.append(p["properties"].get("city", None))
    X, Y = coor_wgs84_to_web_mercator(p["geometry"]["coordinates"][0], p["geometry"]["coordinates"][1])
    coordx.append(X)
    coordy.append(Y)

df = pandas.DataFrame({'country': country, 'capital': capitale, 'coordx': coordx, 'coordy': coordy})
# Convert DataFrame to ColumnDataSource
source = ColumnDataSource(df)

# Create the map with a background
p = figure(x_axis_type="mercator", y_axis_type="mercator", active_scroll="wheel_zoom", title="Capitals of the world",width=1000)
p.add_tile("OSM")

# Create triangles for all coordinates x, y
p.triangle(x="coordx", y="coordy", source=source, size=5)

# Add hover tool to display country and capital names
hover_tool = HoverTool(tooltips=[('Country', '@country'), ('Capital', '@capital')])
p.add_tools(hover_tool)

show(p)


## 4.2 European Countries

In the following example, we demonstrate how to color surfaces on countries, essentially by drawing patches. Each patch is represented by a list of coordinates. The patches are drawn with a list of lists of x coordinates and a list of lists of y coordinates.

In the example below, we focus on several European countries, including those with islands, which require multiple patches per country.

We read the data from the file countries.geojson. This file only contains country codes, not names. Therefore, we use the file capitals.geojson to find the codes based on country names.


In [7]:
from bokeh.plotting import figure, show, output_file
from bokeh.models import HoverTool, ColumnDataSource
import json
import pandas
from bokeh.palettes import Set1
from bokeh.transform import factor_cmap
import numpy as np

# Define the conversion function again
def coor_wgs84_to_web_mercator(lon, lat):
    k = 6378137
    x = lon * (k * np.pi/180.0)
    y = np.log(np.tan((90 + lat) * np.pi/360.0)) * k
    return (x, y)

# Choose the countries to display
my_countries = ["France", "Spain", "Germany", "Portugal", "Italy", "Netherlands", "United Kingdom", "Denmark"]

# Open the capitals file: goal is to find the codes associated with each country
fp2 = open("capitals.geojson", "r", encoding='utf-8')
caps = json.load(fp2)

my_dic_countries = {}
for p in caps["features"]:
    name = p["properties"]["country"]
    code = p["properties"]["iso2"]
    if name in my_countries:
        my_dic_countries[code] = name

# Open the countries file: goal is to get the coordinates of my countries
fp = open("countries.geojson", "r", encoding='utf-8')
dico = json.load(fp)

name = []
coordx = []
coordy = []

for p in dico["features"]:
    code = p["properties"]["cca2"].upper()
    if code in my_dic_countries.keys():
        country = my_dic_countries[code]
        zones = p["geometry"]["coordinates"]
        for poly in zones:
            for liste in poly:
                coord = [coor_wgs84_to_web_mercator(c[0], c[1]) for c in liste]
                coordx.append([c[0] for c in coord])
                coordy.append([c[1] for c in coord])
                name.append(country)

# Create the DataFrame and then the ColumnDataSource
df = pandas.DataFrame({'country': name, 'coordx': coordx, 'coordy': coordy})
source = ColumnDataSource(df)

# Create the figure
p = figure(x_axis_type="mercator", y_axis_type="mercator", active_scroll="wheel_zoom", title="Countries",width=800)
p.add_tile("CartoDb Positron")

# Display the data
p.patches(xs="coordx", ys="coordy", source=source,
          color=factor_cmap('country', palette=Set1[len(my_dic_countries)], factors=list(my_dic_countries.values())), alpha=0.5)

# Hover tool
hover_tool = HoverTool(tooltips=[('Country', '@country')])
p.add_tools(hover_tool)

show(p)


Note that if you zoom in a lot, the borders are not perfect. This is due to the number of points used to produce the patches. More points provide more precise tracing on borders, but a larger coordinate file and slower execution time during rendering.

In [8]:
from bokeh.plotting import figure, show
from bokeh.models import HoverTool, ColumnDataSource
from Exercise4_Source.exercise1_source import analyze_data, access_data_online, coor_wgs84_to_web_mercator

traffic_data = access_data_online()
traffic_df = analyze_data(traffic_data)
traffic_source = ColumnDataSource(traffic_df)

# Output the first few rows of the GeoDataFrame
traffic_df.head()

x  \
0  [-183850.92519664476, -183670.79343442788, -18...   
1  [-183549.47736505227, -183668.95496229743, -18...   
2         [-183008.39560370398, -182763.84087238842]   
3          [-182767.09843482406, -183011.6536510316]   
4  [-182763.65053511283, -182606.80304312822, -18...   

                                                   y   traffic  \
0  [6114325.4890803015, 6114306.854206493, 611429...  freeFlow   
1  [6114312.3686105115, 6114324.730913203, 611434...  freeFlow   
2             [6114362.414099308, 6114407.768890075]  freeFlow   
3              [6114425.441150713, 6114380.08617428]  freeFlow   
4  [6114407.806329003, 6114440.428461959, 6114440...  freeFlow   

                  location                   datetime traffic_color  
0  Route départementale 34  2024-02-01T16:02:00+01:00         green  
1  Route départementale 34  2024-02-01T16:02:00+01:00         green  
2  Route départementale 34  2024-02-01T16:02:00+01:00         green  
3  Route départementale 34  2024-02-01T16:02:00+01:00         green  
4  Route départementale 34  2024-02-01T16:02:00+01:00         green

In [9]:
traffic_df.traffic.unique()

array(['freeFlow', 'heavy', 'congested', 'unknown'], dtype=object)

In [11]:
rennes_coords = coor_wgs84_to_web_mercator(-1.6778, 48.1173)
print(rennes_coords)
zoom_range = 10e3


p = figure(active_scroll="wheel_zoom", title="Traffic Data Visualization", 
        #    x_range=(rennes_coords[0] - zoom_range, rennes_coords[0] + zoom_range),
        #    y_range=(rennes_coords[1] - zoom_range, rennes_coords[1] + zoom_range)
           )


p.add_tile("OSM")
p.multi_line(xs='x', ys='y', source=traffic_source, 
             line_width=5, 
             color='traffic_color')


show(p)

(-186771.8416529544, 6126391.608020729)


In [12]:
from time import sleep

while True:
    traffic_data = access_data_online()
    traffic_df = analyze_data(traffic_data)
    traffic_source = ColumnDataSource(traffic_df)

    p = figure(active_scroll="wheel_zoom", title="Traffic Data Visualization")
    p.add_tile("OSM")
    p.multi_line(xs='x', ys='y', source=traffic_source, 
                line_width=5, 
                color='traffic_color')
    show(p)
    sleep(60)

KeyboardInterrupt: 

In [11]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

In [26]:
import json
import pandas as pd
from bokeh.models import ColumnDataSource
with open("Exercise4_Source/production_2021.json", "r", encoding='utf-8') as f:
    prod_data = json.load(f)

prod_df = pd.DataFrame(prod_data)

prod_source = ColumnDataSource(prod_df)
prod_df

city  photo  bio  hydrau  cogen         pointx  \
0               Saint-Grégoire   40.0    0       0      0 -187610.933354   
1                    Nouvoitou   30.0    0       0      1 -172806.301356   
2              Vezin-le-Coquet   34.0    0       0      0 -194725.858496   
3                      Romillé   65.0    0       0      0 -209138.312707   
4                 Saint-Erblon   21.0    0       0      1 -182853.320993   
5                   Corps-Nuds   37.0    0       0      0 -174789.524208   
6                     Chavagne   43.0    0       0      0 -198877.553859   
7         Chartres-de-Bretagne    NaN    0       0      0 -189961.201392   
8                      Orgères   42.0    0       0      0 -185431.620440   
9       Saint-Sulpice-la-Forêt   14.0    0       0      0 -175425.431344   
10   Saint-Jacques-de-la-Lande    1.0    0       0      0 -191754.280869   
11                      Rennes  177.0    3       0      3 -187224.769269   
12                   Chevaigné   27.0    0       0      0 -182152.850222   
13                       Brécé   26.0    0       0      0 -165844.909058   
14                     Le Rheu    2.0    0       0      0 -198260.840875   
15        Miniac-sous-Bécherel    NaN    0       0      0 -214498.447601   
16                      Acigné   56.0    0       0      0 -169111.774992   
17                 L'Hermitage   34.0    0       0      0 -202194.411484   
18                      Clayes    NaN    0       0      0 -206359.257799   
19                 Saint-Armel   17.0    0       0      0 -175947.526547   
20        La Chapelle-Chaussée   12.0    0       0      0 -207495.567753   
21  Noyal-Châtillon-sur-Seiche   50.0    0       0      1 -185094.093510   
22                  Bourgbarré   39.0    0       0      0 -180604.833256   
23   La Chapelle-des-Fougeretz   31.0    0       0      2 -193842.102187   
24       Parthenay-de-Bretagne   12.0    0       0      0 -203616.530224   
25      La Chapelle-Thouarault   27.0    0       0      0 -206855.587325   
26                   Chantepie   31.0    0       0      0 -178540.820395   
27                      Langan   19.0    0       0      0 -205405.472067   
28                      Gévezé   47.0    1       0      0 -200264.455008   
29                      Laillé   61.0    0       0      0 -190794.573943   
30                   Pont-Péan   20.0    0       0      0 -188839.418853   
31             Vern-sur-Seiche    4.0    0       0      0 -178685.547422   
32                        Bruz   69.0    0       1      0 -194642.706510   
33                   Le Verger   18.0    0       0      0 -215549.941010   
34              Cesson-Sévigné   78.0    0       0      0 -177804.510091   
35                   Mordelles   56.0    0       0      1 -205124.115728   
36                Saint-Gilles   50.0    0       0      0 -206363.809875   
37          Thorigné-Fouillard    NaN    0       0      0 -176378.973731   
38                      Cintré   23.0    1       0      0 -209942.689537   
39                        Pacé    6.0    0       0      0 -197851.386859   
40                    Bécherel    NaN    0       0      0 -216278.590418   
41                 Montgermont   31.0    0       0      0 -191138.449201   
42                      Betton   61.0    0       0      0 -183282.629619   

          pointy                                              zonex  \
0   6.133263e+06  [-190533.15681671872, -190651.05896296108, -19...   
1   6.111944e+06  [-169928.08794255133, -169966.75766198512, -17...   
2   6.126454e+06  [-198323.01525919064, -198265.08047736064, -19...   
3   6.143938e+06  [-212030.07047429672, -212078.96288520907, -21...   
4   6.110002e+06  [-187086.17026896673, -187064.55959358005, -18...   
5   6.103932e+06  [-171258.1967819786, -171399.0026908127, -1715...   
6   6.116230e+06  [-196051.84606495866, -196201.1237210006, -196...   
7   6.114332e+06  [-189188.62920892696, -189371.29714623233, -18...   
8   6.104396e+06  [-182861.2461614804, -18

In [13]:
from bokeh.plotting import figure, show
p = figure(active_scroll="wheel_zoom")
p.add_tile("CartoDb Positron")
p.patches(xs="zonex", ys="zoney", source=prod_source,
          color='blue', alpha=0.5)
show(p)


In [39]:
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, ColorPicker, Legend, LegendItem, CheckboxGroup
from bokeh.palettes import Category10
from bokeh.layouts import column, row

p = figure(title="City Data", active_scroll="wheel_zoom", x_axis_type="mercator", y_axis_type="mercator")
p.add_tile("CartoDb Positron")

colors = Category10[4]

color_pickers = []

for i, category in enumerate(['photo', 'bio', 'hydrau', 'cogen']):
    subset = prod_df[prod_df[category] >= 1]
    subset_source = ColumnDataSource(subset)
    glyph = p.asterisk(x='pointx', y='pointy', source=subset_source, color=colors[i], size=10, legend_label=category)
    picker = ColorPicker(title=f"{category.capitalize()} Color:", color=colors[i])
    picker.js_link('color', glyph.glyph, 'fill_color')
    color_pickers.append(picker)

# Adjust the legend
p.legend.location = 'top_left'
p.legend.click_policy = "hide"

# Layout
layout = row(p, column(*color_pickers))

# Show the plot
show(layout)
